In [1]:
import wshrRelabelLight as WRL
import os
import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler

# 指定文件夹路径
# download_save_path = 'E:/Dataset/wind_shear/Data_Download'
exception_save_path = '../Dataset/Exception_Data'

# 获取文件夹下的所有文件名称
# download_folder_names = [item for item in os.listdir(download_save_path) if os.path.isdir(os.path.join(download_save_path, item))]
exception_folder_names = [item for item in os.listdir(exception_save_path) if os.path.isdir(os.path.join(exception_save_path, item))]
instruction_folder_names = ["@Instructions"]

# 生成所有文件夹路径
# download_folder_paths = [os.path.join(download_save_path, item) for item in download_folder_names]
exception_folder_paths = [os.path.join(exception_save_path, item) for item in exception_folder_names]


In [2]:
# give the preset classification of variables
group_names_list = ["mechanism", "power", "control", "external", "recorder", "unclassified"]
group_lens_dict = {}

var_group_mechanism = ["AIL_1", "AIL_2", "FLAP", "ELEV_1", "ELEV_2", "RUDD", "SPL_1", "SPL_2", "SPLG", "SPLY", "ABRK", "BPGR_1", "BPGR_2", "BPYR_1", "BPYR_2", "MSQT_1", "MSQT_2", "NSQT", "BLV", "CALT", "PACK", "WOW", 
                       "AOA1", "AOA2", "GLS", "PTCH", "ROLL", 
                       "TH", "MH", "TAS", "CASM", "GS", "IVV",
                       "VRTG", "LATG", "LONG", "FPAC", "CTAC"]
var_group_power = ["N2_1", "N2_2", "N2_3", "N2_4",
                   "ECYC_1", "ECYC_2", "ECYC_3", "ECYC_4", "EHRS_1", "EHRS_2", "EHRS_3", "EHRS_4", "VIB_1", "VIB_2", "VIB_3", "VIB_4", "FADS", "HYDG", "HYDY",
                   "N1_1", "N1_2", "N1_3", "N1_4", "N1T", "FF_1", "FF_2", "FF_3", "FF_4", "FQTY_1", "FQTY_2", "FQTY_3", "FQTY_4", "OIP_1", "OIP_2", "OIP_3", "OIP_4", "OIT_1", "OIT_2", "OIT_3", "OIT_4", "OIPL", "EGT_1", "EGT_2", "EGT_3", "EGT_4",
                   "LGDN", "LGUP"]
var_group_control = ["CRSS", "HDGS", "A_T", "APFD", "DFGS", "FGC3", "PUSH", "PTRM", "TCAS",
                     "ILSF", "RUDP", "CCPC", "CCPF", "CWPC", "CWPF", "PLA_1", "PLA_2", "PLA_3", "PLA_4",
                     "SNAP", "TMODE", "EAI", "TAI", "WAI_1", "WAI_2", 
                     "APUF", "FADF", "FIRE_1", "FIRE_2", "FIRE_3", "FIRE_4", "GPWS", "MW", "POVT", "SHKR", "SMOK", "TOCW"]
var_group_external = ["ALT", "ALTR", "WS", "WD", "PI", "PS", "PT", "SAT", "TAT",
                      "DA", "TRK", "TRKM", "LOC", "LATP", "LONP"]
var_group_recorder = ["DWPT", "PH", 
                     "ACMT", "FRMC", "GMT_HOUR", "GMT_MINUTE", "GMT_SEC"]
var_group_unclassified = ["ATEN", "EVNT", "HF1", "HF2", "VHF1", "VHF2", "VHF3", "LMOD", "VMODE", "MACH", "MNS", "MRK", "N1C", "N1CO", "SMKB", "VAR_1107", "VAR_2670", "VAR_5107", "VAR_6670"]

var_groups_dict = {"mechanism": var_group_mechanism, "power": var_group_power, "control": var_group_control, "external": var_group_external, "recorder": var_group_recorder, "unclassified": var_group_unclassified}
for group_name, var_group in var_groups_dict.items():
    group_lens_dict[group_name] = len(var_group)
    print(f"{group_name}: {len(var_group)}")
print(f"\n{sum(group_lens_dict.values())} variables in total")

# 查找给定总序数对应的变量名称
def find_var_name(idx, var_dict):
    count = 0
    group_lens_dict = {}
    for group_name, var_group in var_dict.items():
        group_lens_dict[group_name] = len(var_group)
    for group_name, var_group in var_dict.items():
        if count + group_lens_dict[group_name] > idx:
            return group_name, var_group[idx - count]
        else:
            count += group_lens_dict[group_name]

# 查找给定变量名称对应的总序数
def find_var_idx(var_name, var_dict):
    count = 0
    for var_list in var_dict.values():
        if var_name in var_list:
            count += var_list.index(var_name)
            return(count)
        else:
            count += len(var_list)

mechanism: 38
power: 47
control: 37
external: 15
recorder: 7
unclassified: 19

163 variables in total


In [3]:
'''基于nasa数据集构建训练集、验证集和测试集'''
# 指定读取变量名称
'''
CTSO仿真器输出变量：TIME, ALT, HDOT, VT, ALPHA, GAMMA, PITCH, GREF, WXDT, WZ, VDOT, ALRT
没有WXDT和VDOT的原始数据，GREF不知道什么意思
'''
variable_list = ['ALT', 'ALTR', "TAS", 'GS', 'AOA1', 'AOA2', 'PTCH', 'WS', "WD", 'SAT', 'TAT', 'PI', 'PT']
preset_variable_list = []
for group_list in list(var_groups_dict.values()):
    preset_variable_list.extend(group_list)

# 构建训练集和测试集
train_folder_path = exception_folder_paths[3]
train_mat_name = os.listdir(train_folder_path)[2]
train_X, wshr_train_X = WRL.dataConstruct(train_folder_path, train_mat_name, preset_variable_list, normalized=False)
train_Y, wshr_train_Y = WRL.dataConstruct(train_folder_path, train_mat_name, variable_list, normalized=False)

test_folder_path = exception_folder_paths[3]
test_mat_name = os.listdir(test_folder_path)[8]
test_X, wshr_test_X = WRL.dataConstruct(test_folder_path, test_mat_name, preset_variable_list, normalized=False)
test_Y, wshr_test_Y = WRL.dataConstruct(test_folder_path, test_mat_name, variable_list, normalized=False)

# 计算飞行轨迹角
variable_list.append('GAMMA')
train_Gamma_Y = train_Y[:, 6] - np.mean(train_Y[:, 4:6])
test_Gamma_Y = test_Y[:, 6] - np.mean(test_Y[:, 4:6])

# 重组训练集和测试集数据
train_Y = np.hstack((train_Y, train_Gamma_Y.reshape(-1, 1)))
test_Y = np.hstack((test_Y, test_Gamma_Y.reshape(-1, 1)))

# # 截取海拔位于50~2000英尺的起飞阶段数据
# train_X = train_X[np.where((train_X[:int(train_X.shape[0]/2), 0] >= 50) & (train_X[:int(train_X.shape[0]/2), 0] <= 2000))[0]]
# test_X = test_X[np.where((test_X[:int(test_X.shape[0]/2), 0] >= 50) & (test_X[:int(test_X.shape[0]/2), 0] <= 2000))[0]]
# train_X = train_X[:5000, :]

# 数据集归一化
train_X = StandardScaler().fit_transform(train_X)

s_scaler = StandardScaler()
train_Y = s_scaler.fit_transform(train_Y)
train_mean, train_std = s_scaler.mean_, s_scaler.scale_

test_Y_origin = test_Y
test_X = StandardScaler().fit_transform(test_X)
test_Y = StandardScaler().fit_transform(test_Y)

train_X, test_X = train_Y, test_Y
print(train_X.shape, train_Y.shape, test_X.shape, test_Y.shape)

# 将训练集整理为shape = [batch_size, number_of_timesteps, number_of_time_series]的形式
seq_len = 16
decay_steps = seq_len
pred_steps = 8
train_decay_batch_num = train_X.shape[0] // decay_steps
train_pred_batch_num = train_X.shape[0] // pred_steps
train_batch_X = np.array([train_X[i * decay_steps: (i + 1) * decay_steps, :] for i in range(train_decay_batch_num-1)])
train_batch_Y = np.array([train_Y[(i + 1) * pred_steps: (i + 2) * pred_steps, :] for i in range(train_pred_batch_num-1)])

# 转化为tensor并放到对应设备上
x_train_tensor = torch.from_numpy(train_batch_X).float().to(device)
y_train_tensor = torch.from_numpy(train_batch_Y).float().to(device)

(7852, 14) (7852, 14) (8656, 14) (8656, 14)


In [2]:
# Convolutional transformer 实现
'''
revised based on https://zhuanlan.zhihu.com/p/391337035
卷积相比于原始transformer训练速度更快但收敛速度慢，预测曲线更稳定，但是还是比不上VAR

有待改进：
添加logSparse机制
自注意力计算中/sqrt(d_model)
优化位置编码方式
是否关闭掩码（确定开着）
是否在开始和结尾将k和d_model进行转换
'''
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import numpy as np

device = 'cpu'
if torch.cuda.is_available():
    torch.set_default_tensor_type(torch.cuda.FloatTensor)
    device = 'cuda'

# Self Attention Class
class SelfAttentionConv(nn.Module):
    def __init__(self, k, headers=8, kernel_size=8, mask_next=True, mask_diag=False):
        super().__init__()

        self.k, self.headers, self.kernel_size = k, headers, kernel_size # input_size, header_size, kernel_size
        self.mask_next = mask_next
        self.mask_diag = mask_diag

        h = headers # 注意力头数

        # Query, Key and Value Transformations
        padding = (kernel_size - 1)
        self.padding_opertor = nn.ConstantPad1d((padding, 0), 0) # 该方法将在目标张量的各个维度的首尾各添加padding和0个0值

        # 同源产生Q/K/V矩阵，输入为k维的时序向量，通过多头拆分成k*h个通道，形成kernel_size*k大小的卷积核
        self.toqueries = nn.Conv1d(k, k * h, kernel_size, padding=0, bias=True)
        self.tokeys = nn.Conv1d(k, k * h, kernel_size, padding=0, bias=True)
        self.tovalues = nn.Conv1d(k, k * h, kernel_size=1, padding=0, bias=False)  # No convolution operated
        # kernel_size=1就是原始transformer，>1就是卷积transformer，卷积核能够收集到更多上下文趋势信息

        # Heads unifier
        self.unifyheads = nn.Linear(k * h, k)

    def forward(self, x):
        # Extraction dimensions
        b, t, k = x.size()  # batch_size, number_of_timesteps, input_size

        # Checking Embedding dimension, 
        assert self.k == k, 'Number of time series ' + str(k) + ' didn t much the number of k ' + str(
            self.k) + ' in the initiaalization of the attention layer.'
        h = self.headers

        '''接下来先进行特征层卷积'''

        #  Transpose to see the different time series as different channels
        x = x.transpose(1, 2) # 将最后两个维度转置，获得[batch_size, input_size, number_of_timesteps]形状的张量
        x_padded = self.padding_opertor(x) # 由于padding为0，并没有在张量外围补充0值行列

        # Query, Key and Value Transformations，并将卷积的多头通道拆分
        queries = self.toqueries(x_padded).view(b, k, h, t)
        keys = self.tokeys(x_padded).view(b, k, h, t)
        values = self.tovalues(x).view(b, k, h, t)

        # Transposition to return the canonical format
        queries = queries.transpose(1, 2)  # batch, header, input_size, time step (b, h, k, t)
        queries = queries.transpose(2, 3)  # batch, header, time step, input_size (b, h, t, k)

        values = values.transpose(1, 2)  # batch, header, input_size, time step (b, h, k, t)
        values = values.transpose(2, 3)  # batch, header, time step, input_size (b, h, t, k)

        keys = keys.transpose(1, 2)  # batch, header, input_size, time step (b, h, k, t)
        keys = keys.transpose(2, 3)  # batch, header, time step, input_size (b, h, t, k)

        '''开始计算自注意力矩阵'''

        # Weights
        queries = queries / (k ** (.25))
        keys = keys / (k ** (.25))

        # 将转置后的Q/K/V矩阵进行深拷贝并将不同batch的多头通道合并，即将被分到子空间的原属于不同batch的词向量整合
        queries = queries.transpose(1, 2).contiguous().view(b * h, t, k)
        keys = keys.transpose(1, 2).contiguous().view(b * h, t, k)
        values = values.transpose(1, 2).contiguous().view(b * h, t, k)

        # 计算QK^T， weights是t*t的矩阵
        weights = torch.bmm(queries, keys.transpose(1, 2))

        ## Mask the upper & diag of the attention matrix，使用掩码机制
        if self.mask_next:
            if self.mask_diag:
                indices = torch.triu_indices(t, t, offset=0) # 获取一个t行t列的矩阵的包括对角线和上三角部分元素的[row_idx, cow_idx]
                weights[:, indices[0], indices[1]] = float('-inf') # 屏蔽对角线和上三角部分的注意力权重，即第一轮什么都不知道
            else:
                indices = torch.triu_indices(t, t, offset=1) # 获取一个t行t列的矩阵的上三角部分元素的[row_idx, cow_idx]
                weights[:, indices[0], indices[1]] = float('-inf') # 屏蔽上三角部分的注意力权重，即第一轮是知道一个特征的

        # Softmax
        weights = F.softmax(weights/np.sqrt(k), dim=2)
        '''似乎没有在softmax里比上\sqrt(d_model)？可以防止梯度消失'''

        # Output
        output = torch.bmm(weights, values) # 计算softmax(QK^T)V
        output = output.view(b, h, t, k)
        output = output.transpose(1, 2).contiguous().view(b, t, k * h)

        return self.unifyheads(output)  # shape (b,t,k)

# Conv Transforme Block
class ConvTransformerBLock(nn.Module):
    '''
    自注意力层
    dropout层
    归一化层
    *4 FL
    Relu层
    /4 FL
    归一化层
    '''
    def __init__(self, k, headers, kernel_size=5, mask_next=False, mask_diag=False, dropout_proba=0.2):
        super().__init__()

        # Self attention
        self.attention = SelfAttentionConv(k, headers, kernel_size, mask_next, mask_diag)

        # First & Second Norm
        self.norm1 = nn.LayerNorm(k)
        self.norm2 = nn.LayerNorm(k)

        # Feed Forward Network
        self.feedforward = nn.Sequential(
            nn.Linear(k, 4 * k),
            nn.ReLU(),
            nn.Linear(4 * k, k)
        )

        # Dropout funtcion  & Relu:
        self.dropout = nn.Dropout(p=dropout_proba)
        self.activation = nn.ReLU()

    def forward(self, x, train=False):
        # Self attention + Residual
        x = self.attention(x) + x

        # Dropout attention
        if train:
            x = self.dropout(x)

        # First Normalization
        x = self.norm1(x)

        # Feed Froward network + residual
        x = self.feedforward(x) + x

        # Second Normalization
        x = self.norm2(x)

        return x

# Forcasting Conv Transformer :
class ForcastConvTransformer(nn.Module):
    '''
    位置编码层
    堆叠的卷积tran层
    实现时序压缩的FC层
    '''
    def __init__(self, k, headers, depth, seq_length, pred_len, kernel_size=5, mask_next=True, mask_diag=False, dropout_proba=0.2,
                 num_tokens=None):
        super().__init__()
        # Embedding
        self.tokens_in_count = False
        if num_tokens:
            self.tokens_in_count = True
            self.token_embedding = nn.Embedding(num_tokens, k)  # （369, 1）= (nb_ts, k)

        # Embedding the position，进行位置编码，没有padding填充
        self.position_embedding = nn.Embedding(seq_length, k)   # (500, 1) = (windows_size, k)

        # Number of input channels
        self.k = k  # 没有协变量的情况下，k=1
        self.seq_length = seq_length    # 历史序列长度

        # Transformer blocks
        tblocks = []

        # log sparse 稀疏策略： 采用多层ConvTrans层堆叠的方式
        '''log sparse的思想体现在哪里？应该是没有实现log sparse'''
        for t in range(depth):
            tblocks.append(ConvTransformerBLock(k, headers, kernel_size, mask_next, mask_diag, dropout_proba))
        self.TransformerBlocks = nn.Sequential(*tblocks)

        self.fc = nn.Linear(seq_length, pred_len)

        # # Transformation from k dimension to numClasses
        # self.topreSigma = nn.Linear(k, pred)
        # self.tomu = nn.Linear(k, output_size)
        # self.plus = nn.Softplus() # softplus激活函数

    def forward(self, x, tokens=None):
        b, t, k = x.size()

        # checking that the given batch had same number of time series as the BLock had
        assert k == self.k, 'The k :' + str(
            self.k) + ' number of timeseries given in the initialization is different than what given in the x :' + str(
            k)
        assert t == self.seq_length, 'The lenght of the timeseries given t ' + str(
            t) + ' miss much with the lenght sequence given in the Tranformers initialisation self.seq_length: ' + str(
            self.seq_length)

        # Position embedding
        '''或许可以考虑更好的位置编码方式，通过二维编码乃至更高维编码来反映各维度间元素的相对位置关系'''
        pos = torch.arange(t) # 准备历史长度的向量
        self.pos_emb = self.position_embedding(pos).expand(b, t, k) # 将历史长度向量的位置编码结果扩展（复制）为[b, t, k]的张量

        # Checking token embedding
        assert self.tokens_in_count == (not (tokens is None)), 'self.tokens_in_count = ' + str(
            self.tokens_in_count) + ' should be equal to (not (tokens is None)) = ' + str((not (tokens is None)))
        if not (tokens is None):
            ## checking that the number of tockens corresponde to the number of batch elements
            assert tokens.size(0) == b
            self.tok_emb = self.token_embedding(tokens)
            self.tok_emb = self.tok_emb.expand(t, b, k).transpose(0, 1)

        # Adding Pos Embedding and token Embedding to the variable
        if not (tokens is None):
            x = self.pos_emb + self.tok_emb + x
        else:
            x = self.pos_emb + x # 向输入中添加位置编码

        # Transformer :
        x = self.TransformerBlocks(x)
        # mu = self.tomu(x)
        # presigma = self.topreSigma(x)
        # sigma = self.plus(presigma)

        # # 时间长度变换
        # x = x.transpose(1, 2)
        # x = self.fc(x)
        # x = x.transpose(1, 2)

        # # 将全部特征映射到y特征数的全连接层，全连接层会导致难以收敛
        # x = nn.Linear(k, len(variable_list))(x)

        return x

In [21]:
'''数据准备器，将数据转化为训练集/验证集/测试集'''
import numpy as np
import pandas as pd
import torch
from torch.utils.data import TensorDataset, DataLoader
from sklearn.preprocessing import StandardScaler

device = 'cpu'
if torch.cuda.is_available():
    torch.set_default_tensor_type(torch.cuda.FloatTensor)
    device = 'cuda'
print(device)

class DataPreparer:
    def __init__(self, batch_size, decay_len, pred_len, data_array, out_col_slice):
        self.batch_size = batch_size
        self.decay_len = decay_len
        self.pred_len = pred_len
        self.data = data_array
        self.n_feature = self.data.shape[-1]
        self.out_slice = out_col_slice

        self._prepare_data()

    # 读取数据
    def _prepare_data(self):
        '''
        扩展数据以缩短模型的训练时间至关重要；
        将缩放器安装在训练集上只是为了避免验证和测试集中的数据泄漏
        '''
        # 以0.7/0.2/0.1的比例分割原数据集为训练集/验证集/测试集
        n = self.data.shape[0]
        train_end = int(n * 0.7)
        val_end = n - int(n * 0.1)
        # val_end = train_end
        test_end = n

        train_end = 640
        val_end = train_end
        test_end = n

        train_data = self.data[:train_end]
        val_data = self.data[train_end - self.decay_len : val_end]
        test_data = self.data[val_end - self.decay_len : test_end]

        # standardize by training set
        self.scaler = StandardScaler()
        self.scaler.fit(train_data)

        self.train_data = self.scaler.transform(train_data)
        self.val_data = self.scaler.transform(val_data)
        self.test_data = self.scaler.transform(test_data)

    # 将数据窗口分割为输入和标签
    def _split_window(self, data):
        inputs = data[:, : self.decay_len, :]
        labels = data[:, self.decay_len :, self.out_slice]

        # inputs.set_shape([None, self.decay_len, None])
        # labels.set_shape([None, self.pred_len, None])
        return inputs, labels

    # 将数据重组为[num of samples, seq_len, input_size]的形式
    def _make_dataset(self, data, shuffle=True):
        # 输入的data是[total time length, input_size]的形式
        sample_size = data.shape[0] // (self.decay_len + self.pred_len)
        data = data[: sample_size * (self.decay_len + self.pred_len)]
        data = data.reshape(sample_size, self.decay_len + self.pred_len, self.n_feature)
        # 分割输入和标签
        inputs, labels = self._split_window(data)
        inputs_tensor = torch.tensor(inputs, dtype=torch.float32).to(device)
        labels_tensor = torch.tensor(labels, dtype=torch.float32).to(device)
        # 创建一个 DataLoader
        inputs_loader = DataLoader(inputs_tensor, batch_size=self.batch_size, shuffle=shuffle, generator=torch.Generator(device=device))
        labels_loader = DataLoader(labels_tensor, batch_size=self.batch_size, shuffle=shuffle, generator=torch.Generator(device=device))

        return inputs_loader, labels_loader

    # 通过对预测进行逆变换，生成训练集、验证集和测试集
    def inverse_transform(self, data):
        return self.scaler.inverse_transform(data)

    def get_train(self, shuffle=True):
        # 在训练集中打乱顺序进行训练
        return self._make_dataset(self.train_data, shuffle=shuffle)

    def get_val(self):
        return self._make_dataset(self.val_data, shuffle=False)

    def get_test(self):
        return self._make_dataset(self.test_data, shuffle=False)


cuda


In [18]:
'''基于ctso仿真器数据集构建训练集、验证集和测试集'''
import os

# 规定数据存储位置
train_folder_path = '../Dataset/Simulate_Data/set_1'
train_excel_path = os.path.join(train_folder_path, 'File.xlsx')
train_txt_path = os.path.join(train_folder_path, 'para_info.txt')
test_folder_path = '../Dataset/Simulate_Data/set_3'
test_excel_path = os.path.join(test_folder_path, 'File.xlsx')
test_txt_path = os.path.join(test_folder_path, 'para_info.txt')

# 读取excel数据
train_record_list = pd.read_excel(train_excel_path).values[:, 0]
test_record_list = pd.read_excel(test_excel_path).values[:, 0]
train_data = np.array([list(filter(None, record.split(' '))) for record in train_record_list]).astype('float32')
test_data = np.array([list(filter(None, record.split(' '))) for record in test_record_list]).astype('float32')
origin_data = np.concatenate((train_data, test_data), axis=0)

# 读取变量名称
with open(train_txt_path, 'r') as f:
    variable_list = f.readline().strip().split(', ')

# 筛选用于时序预测的变量列（删除TIME列和ALRT列）
origin_data = origin_data[:, 1:-1]
variable_list.remove('TIME')
variable_list.remove('ALRT')

print(origin_data.shape)
print(variable_list)

# # 规定excel读取位置
# filepath = ('../Dataset/Simulate_Data/set_1/File_indexed.xlsx')
# # 筛选用于时序预测的变量列（删除TIME列和ALRT列）
# df_raw = pd.read_excel(filepath)
# df_pure = df_raw.iloc[:, 1:-1]
# # 提取变量列并将dataframe转化为array
# variable_list = df_pure.columns.tolist()
# origin_data = np.array(df_pure)
# print(variable_list)

# 规定时步频率
time_freq = 4

(956, 10)
['ALT', 'HDOT', 'VT', 'ALPHA', 'GAMMA', 'PITCH', 'GREF', 'WXDT', 'WZ', 'VDOT']


In [67]:
'''基于nasa数据集构建训练集、验证集和测试集'''
import wshrRelabelLight as WRL
import os

# 指定文件夹路径
exception_save_path = '../Dataset/Exception_Data'
# 获取文件夹下的所有文件名称
exception_folder_names = [item for item in os.listdir(exception_save_path) if os.path.isdir(os.path.join(exception_save_path, item))]
# 生成所有文件夹路径
exception_folder_paths = [os.path.join(exception_save_path, item) for item in exception_folder_names]

train_folder_path = exception_folder_paths[3]
train_mat_name = os.listdir(train_folder_path)[2]

variable_list = ['ALT', 'ALTR', "TAS", 'GS', 'AOA1', 'AOA2', 'PTCH', 'WS', "WD", 'SAT', 'TAT', 'PI', 'PT']
origin_data, wshr_label = WRL.dataConstruct(train_folder_path, train_mat_name, variable_list, normalized=False)

# 计算飞行轨迹角
origin_gamma = origin_data[:, 6] - np.mean(origin_data[:, 4:6])
# 重组数据
origin_data = np.hstack((origin_data, origin_gamma.reshape(-1, 1)))
# 重构变量列表
variable_list.append('GAMMA')
print(variable_list)

# 去除20英尺以下的数据
origin_data = origin_data[origin_data[:, 0] > 20]

# 规定时步频率
time_freq = 1

['ALT', 'ALTR', 'TAS', 'GS', 'AOA1', 'AOA2', 'PTCH', 'WS', 'WD', 'SAT', 'TAT', 'PI', 'PT', 'GAMMA']


In [24]:
'''使用ConvSparseTran进行时序预测'''
import plotly.graph_objects as go

# 规定历史序列长度和预测序列长度
decay_len, pred_len = 8, 8
'''如果pred_len>decay_len，会非常难收敛'''

data_preparer = DataPreparer(batch_size=32, decay_len=decay_len, pred_len=pred_len, data_array=origin_data, out_col_slice=slice(0, len(variable_list)))
train_inputs, train_labels = data_preparer.get_train()
val_inputs, val_labels = data_preparer.get_val()
test_inputs, test_labels = data_preparer.get_test()

# 固定随机数
torch.manual_seed(42)

# 构建transformer模型
model = ForcastConvTransformer(k=origin_data.shape[1], headers=8, depth=4, seq_length=decay_len, pred_len=pred_len, mask_next=True)
'''
掩码机制有无目前还不是很影响，删掉的话反而会让模型看到下文信息，掩码遮掉的是时序维度信息，还是遮掉吧
加深堆叠层数并不能显著提升预测效果，反而会大大增加计算成本
'''

# 定义损失函数和优化器
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

# 训练模型
epochs = 2000
train_loss = []
for epoch in range(epochs):
    optimizer.zero_grad()
    epoch_loss = []
    for inputs_tensor, label_tensor in zip(train_inputs, train_labels):
        output = model(inputs_tensor)
        loss = criterion(label_tensor, output)
        loss.backward()
        optimizer.step()
        epoch_loss.append(loss.item())
        print('Epoch [{}/{}], Loss: {:.4f}'.format(epoch+1, epochs, np.mean(epoch_loss)))
    train_loss.extend(epoch_loss)

model.eval()

# 交互式可视化
fig = go.Figure()
fig.add_trace(go.Scatter(y=train_loss, mode='lines', name = 'loss', line = dict(color='blue')))
fig.update_layout(
    # title=f'Train loss on {train_mat_name}',
    title=f'Train loss on CTSO simulation dataset',
    xaxis_title='Train Step',
    yaxis_title='Loss Value'
)
fig.show()


# 使用模型对测试集label进行预测
scaled_preds = []
for inputs_tensor, label_tensor in zip(test_inputs, test_labels):
    output = model(inputs_tensor)
    scaled_preds.extend(output.detach().cpu().numpy())
scaled_preds = np.array(scaled_preds)
scaled_preds = scaled_preds.reshape(-1, scaled_preds.shape[-1])

# 以训练集的均值和方差还原为原始量纲
preds = data_preparer.inverse_transform(scaled_preds)

for label_tensor in test_labels:
    label_array = label_tensor.cpu().numpy()
    label_array = label_array.reshape(-1, label_array.shape[-1]) # 转化成[total time length, input_size]的形状
    GT = data_preparer.inverse_transform(label_array)
    for idx in range(len(variable_list)):
        fig = go.Figure()
        # fig.add_trace(go.Scatter(y=test_X_origin[:decay_steps+pred_steps, idx], mode='lines', name = 'GT', line = dict(color='blue')))
        fig.add_trace(go.Scatter(x=[i/time_freq for i in range(GT.shape[0])], y=GT[:, idx], mode='lines', name = 'GT', line = dict(color='blue')))
        fig.add_trace(go.Scatter(x=[i/time_freq for i in range(preds.shape[0])], y=preds[:, idx], mode='lines', name = 'pred', line = dict(color='red')))
        fig.update_layout(
            title=f'TSMixer Prediction vs. Ground Truth for {variable_list[idx]}',
            xaxis_title='Time Step',
            yaxis_title='Value'
        )
        fig.show()


# 使用模型对测试集全程进行时序预测
scaler = StandardScaler()
scaler.fit(origin_data)
all_scaled_GT = scaler.transform(origin_data)

all_scaled_preds = []
for start in range(0, all_scaled_GT.shape[0] - decay_len - pred_len):
    input_tensor = torch.from_numpy(all_scaled_GT[start:start+decay_len].astype(np.float32)).to(device)
    input_tensor = input_tensor.unsqueeze(0)
    output = model(input_tensor)
    output = output.to('cpu').detach().numpy()[0]
    # print(pred_results.shape)
    if start == 0:
        all_scaled_preds = np.vstack((all_scaled_GT[:decay_len], output))
        # print(test_X_pred.shape)
    else:
        all_scaled_preds = np.vstack((all_scaled_preds, output[-1, :]))
all_scaled_preds = np.array(all_scaled_preds)
all_preds = scaler.inverse_transform(all_scaled_preds)
print(origin_data.shape, all_preds.shape)

for idx in range(len(variable_list)):
    fig = go.Figure()
    # fig.add_trace(go.Scatter(y=test_X_origin[:decay_steps+pred_steps, idx], mode='lines', name = 'GT', line = dict(color='blue')))
    fig.add_trace(go.Scatter(x=[i/time_freq for i in range(origin_data.shape[0])], y=origin_data[:, idx], mode='lines', name = 'GT', line = dict(color='blue')))
    fig.add_trace(go.Scatter(x=[i/time_freq for i in range(all_preds.shape[0])], y=all_preds[:, idx], mode='lines', name = 'pred', line = dict(color='red')))
    fig.add_vline(x=160, line_width=1, line_dash="dash", line_color="purple")
    fig.update_layout(
        title=f'Conv. Transformer Prediction vs. Ground Truth for {variable_list[idx]}',
        xaxis_title='Time Step',
        yaxis_title='Value'
    )
    fig.show()

Epoch [1/2000], Loss: 0.9543
Epoch [1/2000], Loss: 1.1264
Epoch [2/2000], Loss: 0.9426
Epoch [2/2000], Loss: 0.8546
Epoch [3/2000], Loss: 0.8746
Epoch [3/2000], Loss: 0.7304
Epoch [4/2000], Loss: 0.7689
Epoch [4/2000], Loss: 0.7016
Epoch [5/2000], Loss: 0.6765
Epoch [5/2000], Loss: 0.6969
Epoch [6/2000], Loss: 0.6801
Epoch [6/2000], Loss: 0.5781
Epoch [7/2000], Loss: 0.6263
Epoch [7/2000], Loss: 0.5577
Epoch [8/2000], Loss: 0.5430
Epoch [8/2000], Loss: 0.5946
Epoch [9/2000], Loss: 0.5612
Epoch [9/2000], Loss: 0.4945
Epoch [10/2000], Loss: 0.5329
Epoch [10/2000], Loss: 0.4709
Epoch [11/2000], Loss: 0.4606
Epoch [11/2000], Loss: 0.5220
Epoch [12/2000], Loss: 0.4557
Epoch [12/2000], Loss: 0.4835
Epoch [13/2000], Loss: 0.4417
Epoch [13/2000], Loss: 0.4672
Epoch [14/2000], Loss: 0.4025
Epoch [14/2000], Loss: 0.4907
Epoch [15/2000], Loss: 0.4095
Epoch [15/2000], Loss: 0.4458
Epoch [16/2000], Loss: 0.4258
Epoch [16/2000], Loss: 0.3933
Epoch [17/2000], Loss: 0.4005
Epoch [17/2000], Loss: 0.403

(956, 10) (955, 10)


In [7]:
# 原始transformer，用全连接做解码器
'''
结果基本就是在pred_steps将之前的数据变化复读一遍
'''

import torch
import torch.nn as nn
import torch.optim as optim
import numpy as np

device = 'cpu'
if torch.cuda.is_available():
    torch.set_default_tensor_type(torch.cuda.FloatTensor)
    device = 'cuda'

# 构建Transformer模型
class TransformerModel(nn.Module):
    def __init__(self, input_dim, output_dim, seq_len, num_layers, d_model, num_heads, d_ff, dropout):
        super(TransformerModel, self).__init__()
        
        self.embedding = nn.Linear(input_dim, d_model)
        self.positional_encoding = PositionalEncoding(d_model, dropout, seq_len)
        self.transformer_encoder = nn.TransformerEncoder(
            nn.TransformerEncoderLayer(d_model, num_heads, d_ff, dropout),
            num_layers
        )
        self.decoder = nn.Linear(d_model, output_dim)
    
    def forward(self, x):
        x = self.embedding(x)  # 输入数据经过线性变换
        x = self.positional_encoding(x)  # 加入位置编码
        x = self.transformer_encoder(x)  # Transformer编码器
        x = self.decoder(x)  # 解码成目标维度
        return x

# 位置编码
class PositionalEncoding(nn.Module):
    def __init__(self, d_model, dropout, max_len=5000):
        super(PositionalEncoding, self).__init__()
        self.dropout = nn.Dropout(p=dropout)
        
        pe = torch.zeros(max_len, d_model)
        position = torch.arange(0, max_len, dtype=torch.float).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() * (-np.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)
        pe = pe.unsqueeze(0)
        self.register_buffer('pe', pe)
    
    def forward(self, x):
        x = x + self.pe[:, :x.size(1)]
        return self.dropout(x)

# 构建训练和测试数据
input_dim = train_X.shape[1]  # 输入维度
output_dim = train_X.shape[1]  # 输出维度
seq_len = 15  # 时间序列长度
num_layers = 5  # Transformer层数，层数20难以收敛
d_model = 64  # 模型特征维度，必须是header的整数倍，过多的特征数会使得预测曲线变化微弱
num_heads = 8  # 注意力头数
d_ff = 128  # 前馈神经网络的隐藏层维度
dropout = 0.1  # Dropout概率

# 将训练集整理为shape = [batch_size, number_of_timesteps, number_of_time_series]的形式
decay_steps = seq_len
pred_steps = seq_len
train_decay_batch_num = train_X.shape[0] // decay_steps
train_pred_batch_num = train_X.shape[0] // pred_steps
train_batch_X = np.array([train_X[i * decay_steps: (i + 1) * decay_steps, :] for i in range(train_decay_batch_num-1)])
train_batch_Y = np.array([train_Y[(i + 1) * pred_steps: (i + 2) * pred_steps, :] for i in range(train_pred_batch_num-1)])

# 转化为tensor并放到对应设备上
x_train_tensor = torch.from_numpy(train_batch_X).float().to(device)
y_train_tensor = torch.from_numpy(train_batch_Y).float().to(device)

# 初始化Transformer模型
model = TransformerModel(input_dim, output_dim, seq_len, num_layers, d_model, num_heads, d_ff, dropout)

# 定义损失函数和优化器
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

# 训练模型
epochs = 200
train_loss = []
for epoch in range(epochs):
    optimizer.zero_grad()
    output = model(x_train_tensor)
    loss = criterion(output, y_train_tensor)
    loss.backward()
    optimizer.step()
    train_loss.append(loss.item())
    print('Epoch [{}/{}], Loss: {:.4f}'.format(epoch+1, epochs, loss.item()))

# 使用模型进行预测
test_Y_pred = None
for start in range(0, test_X.shape[0] - pred_steps - decay_steps + 1):
    test_input = torch.from_numpy(test_X[start:start+decay_steps].astype(np.float32)).to(device)
    test_input = test_input.unsqueeze(0)
    pred_results = model(test_input)
    pred_results = pred_results.to('cpu').detach().numpy()[0]
    # print(pred_results.shape)
    if start == 0:
        test_Y_pred = np.vstack((test_Y[:decay_steps], pred_results))
        # print(test_X_pred.shape)
    else:
        test_Y_pred = np.vstack((test_Y_pred, pred_results[-1, :]))
    # break
        
# 以训练集的均值和方差还原为原始量纲
test_Y_pred = test_Y_pred * train_std + train_mean

import plotly.graph_objects as go

# 交互式可视化
fig = go.Figure()
fig.add_trace(go.Scatter(y=train_loss, mode='lines', name = 'loss', line = dict(color='blue')))
fig.update_layout(
    title=f'Train loss on {train_mat_name}',
    xaxis_title='Time Step',
    yaxis_title='Loss Value'
)
fig.show()

for idx in range(len(variable_list)):
    fig = go.Figure()
    # fig.add_trace(go.Scatter(y=test_X_origin[:decay_steps+pred_steps, idx], mode='lines', name = 'GT', line = dict(color='blue')))
    fig.add_trace(go.Scatter(y=test_Y_origin[:, idx], mode='lines', name = 'GT', line = dict(color='blue')))
    fig.add_trace(go.Scatter(y=test_Y_pred[:, idx], mode='lines', name = 'pred', line = dict(color='red')))
    fig.update_layout(
        title=f'Transformer Prediction vs. Ground Truth for {variable_list[idx]}',
        xaxis_title='Time Step',
        yaxis_title='Value'
    )
    fig.show()


Epoch [1/200], Loss: 1.5217
Epoch [2/200], Loss: 1.1318
Epoch [3/200], Loss: 1.0637
Epoch [4/200], Loss: 0.9840


Epoch [5/200], Loss: 0.9143
Epoch [6/200], Loss: 0.8724
Epoch [7/200], Loss: 0.8429
Epoch [8/200], Loss: 0.8093
Epoch [9/200], Loss: 0.7653
Epoch [10/200], Loss: 0.7092
Epoch [11/200], Loss: 0.6464
Epoch [12/200], Loss: 0.5838
Epoch [13/200], Loss: 0.5304
Epoch [14/200], Loss: 0.4859
Epoch [15/200], Loss: 0.4473
Epoch [16/200], Loss: 0.4141
Epoch [17/200], Loss: 0.3824
Epoch [18/200], Loss: 0.3575
Epoch [19/200], Loss: 0.3372
Epoch [20/200], Loss: 0.3155
Epoch [21/200], Loss: 0.2973
Epoch [22/200], Loss: 0.2814
Epoch [23/200], Loss: 0.2670
Epoch [24/200], Loss: 0.2536
Epoch [25/200], Loss: 0.2429
Epoch [26/200], Loss: 0.2311
Epoch [27/200], Loss: 0.2213
Epoch [28/200], Loss: 0.2128
Epoch [29/200], Loss: 0.2047
Epoch [30/200], Loss: 0.1941
Epoch [31/200], Loss: 0.1875
Epoch [32/200], Loss: 0.1787
Epoch [33/200], Loss: 0.1724
Epoch [34/200], Loss: 0.1678
Epoch [35/200], Loss: 0.1624
Epoch [36/200], Loss: 0.1567
Epoch [37/200], Loss: 0.1521
Epoch [38/200], Loss: 0.1485
Epoch [39/200], Los